### Details [1]

Name: MountainCar
Framework: OpenAI GYM
[Webpage](https://gym.openai.com/envs/MountainCar-v0)

### Description

Get an under powered car to the top of a hill (top = 0.5 position). A car is on a one-dimensional track, positioned between two "mountains". The goal is to drive up the mountain on the right; however, the car's engine is not strong enough to scale the mountain in a single pass. Therefore, the only way to succeed is to drive back and forth to build up momentum.


## Source

Andrew Moore in his PhD thesis [Moore90].

### Environment

## Observation

Type: Box(2)

Num | Observation  | Min  | Max  
----|--------------|------|----   
0   | position     | -1.2 | 0.6
1   | velocity     | -0.07| 0.07


## Actions

Type: Discrete(3)

Num | Observation |
----|-------------|
0   | push left   |
1   | no push     |
2   | push right  |

## Reward

-1 for each time step, until the goal position of 0.5 is reached.

## Starting State

Random position from -0.6 to -0.4 with no velocity.

## Episode Termination

The episode ends when you reach 0.5 position

## Solution Requirements

Getting average reward of -110.0 over 100 consecutive trials.

![Mountain Car](images/mountaincar.png)

## Solution Design

### Feature Representation
Linear in the parameters for each action
\begin{align}
[s,  v,  s*v,  s^2,  v^2,  s^2*v,  s*v^2]
\end{align}

### State Action Value Estimate
$$\begin{eqnarray}
Q(s, a)' &=& \vec{\theta_t^T} \vec{\phi_s} &=&  \sum_{i=1}^n \vec{\theta_t}(i) \vec{\phi_s}(i)
\end{eqnarray}$$

### Weight update quantity(gradient)
\begin{align}
\nabla_\vec{\theta_t} V_t (s) &= \vec{\phi_s}
\end{align}

In [9]:
import io
import base64
from IPython.display import HTMLT
import gym
from gym import wrappers
import numpy as np
import random

#All_constants

In [ ]:
#Make sure you change this variable whenever you change the number of features space components
features_per_action = 7

In [ ]:
class Agent():
    def __init__(self, env, step_size = 0.05, gamma = 0.95, horizon = 30):
        self.step_size = step_size
        self.env = env
        self.gamma = gamma
        self.weights = ((2 * np.random.ranf([( features_per_action * self.env.action_space.n ) + 1])) - 1)/2.0
        self.EPSILON = 1
        self.HORIZON = horizon

    def doFunctionApproximationFromStateActionPair(self, episode_step):
        feature_vector  = self.getFeatureVector(episode_step)
        return np.dot(feature_vector, self.weights)

    def updateFunctionApproximator(self, episode):
        for episode_step_iterator in range(len(episode)):
            #print(str(episode_step_iterator))
            episode_step = episode[episode_step_iterator]
            discounted_return = self.getDiscountedReturn(episode[episode_step_iterator:])
            current_estimated_value = self.doFunctionApproximationFromStateActionPair(episode_step)
            delta_weights = np.multiply(np.multiply(self.step_size, self.getFeatureVector(episode_step)), (discounted_return - current_estimated_value))
            self.weights = self.weights + delta_weights
        print("Updated")

    def getDiscountedReturn(self, episode):
        discounted_return = 0.0
        effective_discounting = 1.0
        horizon_iterator = 0
        for episode_step in episode:
            if horizon_iterator > self.HORIZON:
                break
            discounted_return = discounted_return + (effective_discounting * episode_step[-1])
            effective_discounting *= self.gamma
            horizon_iterator += 1
        return discounted_return

    def start(self):
        observation = self.env.reset()
        episode_counter = 0
        while(True):
            print('Episode number', str(episode_counter))
            random_throw = random.uniform(0, 1)
            if random_throw < self.EPSILON:
                episode = self.drawEpisodeStochastically()
            else:
                episode = self.drawEpisodeGreedily()
            self.updateFunctionApproximator(episode)
            episode_counter += 1
            self.EPSILON = max(0.25, (self.EPSILON * 0.8))

    def drawEpisodeStochastically(self):
        episode = []
        print('Stochastic')
        observation = self.env.reset()
        done = False
        while(not done):
            #self.env.render()

            episode_step = [observation]

            action = self.env.action_space.sample()
            episode_step.append(action)

            observation, reward, done, info = self.env.step(action)
            episode_step.append(reward)
            episode.append(episode_step)

            #print('Step taken')

        return episode

    def drawEpisodeGreedily(self):
        episode = []
        print('Greedy')
        observation = self.env.reset()
        done = False
        while(not done):
            #self.env.render()
            episode_step = [observation]

            best_action = self.env.action_space.sample()
            best_value = self.doFunctionApproximationFromStateActionPair([observation, best_action])
            for action_iterator in range(self.env.action_space.n):
                value = self.doFunctionApproximationFromStateActionPair([observation, action_iterator])
                if value > best_value:
                    best_action = action_iterator
                    best_value = value

            episode_step.append(best_action)

            observation, reward, done, info = self.env.step(best_action)
            episode_step.append(reward)

            episode.append(episode_step)

        return episode

    def getFeatureVector(self, episode_step):
        observation = episode_step[0]
        action = episode_step[1]
        feature_vector = [1]
        for action_iterator in range(self.env.action_space.n):
            if action_iterator == action:
                feature_vector.append(observation[0])
                feature_vector.append(observation[1])
                feature_vector.append(observation[0]*observation[1])
                feature_vector.append(observation[0]*observation[0])
                feature_vector.append(observation[1]*observation[1])
                feature_vector.append(observation[0]*observation[1]*observation[1])
                feature_vector.append(observation[0]*observation[0]*observation[1])
            else:
                for feature_iterator in range(features_per_action):
                    feature_vector.append(0)
        return feature_vector

In [ ]:
env = gym.make('MountainCarModified-v0')
env = wrappers.Monitor(env, './recordings/mountain_car', force=True)
agent = Agent(env, step_size= 0.05, gamma = 1)
agent.start()

In [10]:
filename = 'Batman.mp4'

video = io.open(filename, 'r+b').read()
encoded = base64.b64encode(video)
HTML(data='''<video alt="AstroML talk" controls>
           <source src="data:video/mp4;base64,{0}" type="video/mp4" />
           </video>'''.format(encoded.decode('ascii')))

## Challenges
The number of allowed number of episode steps were only 200. An sample run on the environment showed that any naive stochastic search would take thousands or even hundred thousands of steps in an episode to reach the goal state. The restriction to just 200 is too small. However, this is due to the reason that OpenAI wants to put forward challenging problems for the world to solve. One of them is how to be smart about exploration.
## Solution
I have to manually edit the OpenAI source code to allow my agent to take much more number of steps than 200. However, OpenAI discourages uploading such simulation results as there is no novelty in such implementations.

### Room for improvement in the horizon
* Can try Coarse Feature Coding.
* Can try Tile Feature Coding.
* Can use RBF for feature encoding.
* Can use neural network, or even deep neural network as function approximator.
* Can use planning as in Dyna Architecture for faster convergence.

### References:
* https://github.com/openai/gym/wiki/MountainCar-v0
* https://gym.openai.com/envs/MountainCar-v0